In [1]:
import numpy as np
import math
import plotly.offline as py
import plotly.graph_objs as go

py.init_notebook_mode()
np.random.seed(0)

# Creating the noisy sphere

The main idea is just to
sample points from a given sphere, and meshing them to create a plain sphere.
If the resolution is high, more points will be sampled but it will take more
time for the CPU to generate the surface.
We can use spherical coordinates to sample the pooints given a sphere and the angles.
We need a minimum of 4 points, indeed there are 3 equations but 4 parameters (x,y,z,r)

In [2]:
def mGeneratePointsFromSphere(model, nPoints):
    res = int(np.ceil(math.sqrt(nPoints)))
    theta = np.linspace(0,2*np.pi,res)
    phi = np.linspace(0,np.pi,res)
    
    x = model[3]*np.outer(np.cos(theta),np.sin(phi))
    y = model[3]*np.outer(np.sin(theta),np.sin(phi))
    z = model[3]*np.outer(np.ones(res),np.cos(phi))
    
    X = x + model[0]
    Y = y + model[1]
    Z = z + model[2]
    
    points = np.zeros((nPoints, 3))
    points[:,0] = X.ravel()[0:nPoints]
    points[:,1] = Y.ravel()[0:nPoints]
    points[:,2] = Z.ravel()[0:nPoints]

    return points, X, Y, Z

sphModel = [1, 2, 4, 10]
nPoints = 500
sphPoints = mGeneratePointsFromSphere(sphModel, nPoints)[0] + np.random.randn(nPoints,3)/2

Given these points, the error function to be minimized is 
https://www.geometrictools.com/Documentation/LeastSquaresFitting.pdf p.9
The basic idea is just to compute the radius given one point (x,y,z).
Then it is possible to compare it to the true radius.
We do that for every points using a square loss function

In [3]:
# derivative of E by r is
#    \begin{equation}
#    \frac{\delta E}{\delta r} = -2\Sum_{i=1}^m (L_i -r)
    #\end{equation}
    
    # derivative of L_i by a is
#    \begin{equation}
#    \frac{\delta L_i}{\delta a} = \frac{a-x_i}{\sqrt{(x_i-a)^2 + (y_i-b)^2 + (z_i-c)^2}}
    #\end{equation}
    
    # derivative of E by a is
#    \begin{equation}
#    \frac{\delta E}{\delta a} = 2\Sum_{i=1}{m}((x_i-a) + r\frac{\delta L_i}{\delta a})
    #\end{equation}
    
        # derivative of L_i by b is
#    \begin{equation}
#    \frac{\delta L_i}{\delta b} = \frac{b-y_i}{\sqrt{(x_i-a)^2 + (y_i-b)^2 + (z_i-c)^2}}
    #\end{equation}

    # derivative of E by b is
#    \begin{equation}
#    \frac{\delta E}{\delta b} = 2\Sum_{i=1}{m}((y_i-b) + r\frac{\delta L_i}{\delta b})
    #\end{equation}
    
        # derivative of L_i by c is
#    \begin{equation}
#    \frac{\delta L_i}{\delta c} = \frac{c-z_i}{\sqrt{(x_i-a)^2 + (y_i-b)^2 + (z_i-c)^2}}
    #\end{equation}

    # derivative of E by c is
#    \begin{equation}
#    \frac{\delta E}{\delta c} = 2\Sum_{i=1}{m}((z_i-c) + r\frac{\delta L_i}{\delta c})
    #\end{equation}

def mSphLoss(T, x):
    L = np.sqrt((x[:,0] - T[0])**2 + (x[:,1] - T[1])**2 + (x[:,2] - T[2])**2)
    return L

def cost_function(T, x):
    L = mSphLoss(T, x)
    return np.sum( (L - T[3])**2 )

def derivative_cost_function(T, x):
    L = mSphLoss(T, x)
    
    dr = (-1)*(-2)*np.sum( (L - T[3]) )
    
    dLa = (T[0] - x[:,0])/L
    da = 2*np.sum( (x[:,0] - T[0]) + T[3]*dLa )
    
    dLb = (T[1] - x[:,1])/L
    db = 2*np.sum( (x[:,1] - T[1]) + T[3]*dLb )
    
    dLc = (T[2] - x[:,2])/L
    dc = 2*np.sum( (x[:,2] - T[2]) + T[3]*dLc )
    
    return np.array([da, db, dc, dr])

# To do gradient descent, we need to find the partial derivative.

In [4]:
T = np.array([0, 0, 0, 10]) #initial guess
learnRate = 1e-5
iterMax = 10000
grad = [1e99, 1e99, 1e99]

lkls = []
params = []

for it in range(iterMax): 
    if( abs(np.sum(grad))<1e-6 ):
        continue
    # gradient descent
    grad = derivative_cost_function(T, sphPoints)
    print("### Epoch %d : [%1.4e, %1.4e, %1.4e, %1.4e]" %(it, grad[0], grad[1], grad[2], grad[3]))
    T = T + learnRate*grad

print("Done !")

# We use the formula for the radius
print(T)

### Epoch 0 : [2.3497e+02, 4.4028e+02, 1.9991e+03, 6.1965e+02]
### Epoch 1 : [2.3421e+02, 4.3892e+02, 1.9886e+03, 6.0844e+02]
### Epoch 2 : [2.3346e+02, 4.3758e+02, 1.9781e+03, 5.9739e+02]
### Epoch 3 : [2.3272e+02, 4.3626e+02, 1.9678e+03, 5.8650e+02]
### Epoch 4 : [2.3198e+02, 4.3495e+02, 1.9575e+03, 5.7576e+02]
### Epoch 5 : [2.3125e+02, 4.3366e+02, 1.9472e+03, 5.6518e+02]
### Epoch 6 : [2.3053e+02, 4.3238e+02, 1.9371e+03, 5.5475e+02]
### Epoch 7 : [2.2982e+02, 4.3112e+02, 1.9270e+03, 5.4447e+02]
### Epoch 8 : [2.2912e+02, 4.2987e+02, 1.9170e+03, 5.3433e+02]
### Epoch 9 : [2.2842e+02, 4.2864e+02, 1.9070e+03, 5.2435e+02]
### Epoch 10 : [2.2773e+02, 4.2742e+02, 1.8971e+03, 5.1450e+02]
### Epoch 11 : [2.2704e+02, 4.2621e+02, 1.8873e+03, 5.0480e+02]
### Epoch 12 : [2.2636e+02, 4.2502e+02, 1.8776e+03, 4.9524e+02]
### Epoch 13 : [2.2569e+02, 4.2384e+02, 1.8679e+03, 4.8582e+02]
### Epoch 14 : [2.2502e+02, 4.2267e+02, 1.8583e+03, 4.7653e+02]
### Epoch 15 : [2.2437e+02, 4.2152e+02, 1.8487e+03

### Epoch 762 : [3.8704e+01, 8.3956e+01, 4.2561e+01, -6.3064e+00]
### Epoch 763 : [3.8608e+01, 8.3756e+01, 4.2340e+01, -6.2719e+00]
### Epoch 764 : [3.8513e+01, 8.3557e+01, 4.2120e+01, -6.2376e+00]
### Epoch 765 : [3.8418e+01, 8.3358e+01, 4.1902e+01, -6.2034e+00]
### Epoch 766 : [3.8323e+01, 8.3160e+01, 4.1684e+01, -6.1695e+00]
### Epoch 767 : [3.8229e+01, 8.2962e+01, 4.1468e+01, -6.1358e+00]
### Epoch 768 : [3.8134e+01, 8.2765e+01, 4.1252e+01, -6.1022e+00]
### Epoch 769 : [3.8040e+01, 8.2568e+01, 4.1038e+01, -6.0688e+00]
### Epoch 770 : [3.7946e+01, 8.2372e+01, 4.0825e+01, -6.0356e+00]
### Epoch 771 : [3.7853e+01, 8.2176e+01, 4.0613e+01, -6.0026e+00]
### Epoch 772 : [3.7759e+01, 8.1980e+01, 4.0402e+01, -5.9698e+00]
### Epoch 773 : [3.7666e+01, 8.1785e+01, 4.0192e+01, -5.9372e+00]
### Epoch 774 : [3.7573e+01, 8.1591e+01, 3.9984e+01, -5.9047e+00]
### Epoch 775 : [3.7480e+01, 8.1396e+01, 3.9776e+01, -5.8724e+00]
### Epoch 776 : [3.7388e+01, 8.1203e+01, 3.9569e+01, -5.8403e+00]
### Epoch 

### Epoch 1038 : [1.9585e+01, 4.3386e+01, 1.0027e+01, -1.4067e+00]
### Epoch 1039 : [1.9537e+01, 4.3282e+01, 9.9740e+00, -1.3991e+00]
### Epoch 1040 : [1.9489e+01, 4.3178e+01, 9.9215e+00, -1.3916e+00]
### Epoch 1041 : [1.9441e+01, 4.3075e+01, 9.8693e+00, -1.3840e+00]
### Epoch 1042 : [1.9393e+01, 4.2971e+01, 9.8174e+00, -1.3766e+00]
### Epoch 1043 : [1.9346e+01, 4.2868e+01, 9.7657e+00, -1.3691e+00]
### Epoch 1044 : [1.9298e+01, 4.2766e+01, 9.7143e+00, -1.3617e+00]
### Epoch 1045 : [1.9251e+01, 4.2663e+01, 9.6632e+00, -1.3544e+00]
### Epoch 1046 : [1.9203e+01, 4.2561e+01, 9.6123e+00, -1.3471e+00]
### Epoch 1047 : [1.9156e+01, 4.2459e+01, 9.5617e+00, -1.3398e+00]
### Epoch 1048 : [1.9109e+01, 4.2357e+01, 9.5114e+00, -1.3325e+00]
### Epoch 1049 : [1.9062e+01, 4.2256e+01, 9.4613e+00, -1.3253e+00]
### Epoch 1050 : [1.9015e+01, 4.2155e+01, 9.4115e+00, -1.3182e+00]
### Epoch 1051 : [1.8968e+01, 4.2054e+01, 9.3619e+00, -1.3111e+00]
### Epoch 1052 : [1.8921e+01, 4.1953e+01, 9.3126e+00, -1.3040e

### Epoch 1465 : [6.8597e+00, 1.5562e+01, 1.0076e+00, -1.2590e-01]
### Epoch 1466 : [6.8429e+00, 1.5524e+01, 1.0020e+00, -1.2512e-01]
### Epoch 1467 : [6.8261e+00, 1.5487e+01, 9.9649e-01, -1.2435e-01]
### Epoch 1468 : [6.8094e+00, 1.5450e+01, 9.9098e-01, -1.2358e-01]
### Epoch 1469 : [6.7927e+00, 1.5413e+01, 9.8550e-01, -1.2282e-01]
### Epoch 1470 : [6.7761e+00, 1.5376e+01, 9.8005e-01, -1.2206e-01]
### Epoch 1471 : [6.7595e+00, 1.5339e+01, 9.7462e-01, -1.2131e-01]
### Epoch 1472 : [6.7430e+00, 1.5302e+01, 9.6923e-01, -1.2056e-01]
### Epoch 1473 : [6.7264e+00, 1.5265e+01, 9.6386e-01, -1.1981e-01]
### Epoch 1474 : [6.7100e+00, 1.5229e+01, 9.5852e-01, -1.1907e-01]
### Epoch 1475 : [6.6935e+00, 1.5192e+01, 9.5321e-01, -1.1833e-01]
### Epoch 1476 : [6.6772e+00, 1.5156e+01, 9.4793e-01, -1.1759e-01]
### Epoch 1477 : [6.6608e+00, 1.5119e+01, 9.4268e-01, -1.1686e-01]
### Epoch 1478 : [6.6445e+00, 1.5083e+01, 9.3746e-01, -1.1614e-01]
### Epoch 1479 : [6.6282e+00, 1.5047e+01, 9.3226e-01, -1.1541e

### Epoch 1965 : [2.0156e+00, 4.6811e+00, 4.5848e-02, 2.7611e-03]
### Epoch 1966 : [2.0107e+00, 4.6698e+00, 4.5502e-02, 2.7951e-03]
### Epoch 1967 : [2.0058e+00, 4.6586e+00, 4.5158e-02, 2.8290e-03]
### Epoch 1968 : [2.0009e+00, 4.6474e+00, 4.4816e-02, 2.8625e-03]
### Epoch 1969 : [1.9960e+00, 4.6363e+00, 4.4475e-02, 2.8957e-03]
### Epoch 1970 : [1.9911e+00, 4.6252e+00, 4.4137e-02, 2.9287e-03]
### Epoch 1971 : [1.9862e+00, 4.6141e+00, 4.3801e-02, 2.9614e-03]
### Epoch 1972 : [1.9814e+00, 4.6030e+00, 4.3467e-02, 2.9938e-03]
### Epoch 1973 : [1.9765e+00, 4.5919e+00, 4.3135e-02, 3.0260e-03]
### Epoch 1974 : [1.9717e+00, 4.5809e+00, 4.2805e-02, 3.0579e-03]
### Epoch 1975 : [1.9669e+00, 4.5699e+00, 4.2477e-02, 3.0895e-03]
### Epoch 1976 : [1.9621e+00, 4.5590e+00, 4.2151e-02, 3.1209e-03]
### Epoch 1977 : [1.9573e+00, 4.5480e+00, 4.1826e-02, 3.1520e-03]
### Epoch 1978 : [1.9525e+00, 4.5371e+00, 4.1504e-02, 3.1828e-03]
### Epoch 1979 : [1.9477e+00, 4.5262e+00, 4.1184e-02, 3.2134e-03]
### Epoch 

...

### Epoch 6460 : [3.2967e-05, 9.5963e-05, -6.9807e-07, 3.6206e-07]
### Epoch 6461 : [3.2886e-05, 9.5733e-05, -6.9637e-07, 3.6118e-07]
### Epoch 6462 : [3.2805e-05, 9.5504e-05, -6.9467e-07, 3.6031e-07]
### Epoch 6463 : [3.2724e-05, 9.5275e-05, -6.9298e-07, 3.5944e-07]
### Epoch 6464 : [3.2644e-05, 9.5046e-05, -6.9129e-07, 3.5857e-07]
### Epoch 6465 : [3.2564e-05, 9.4818e-05, -6.8960e-07, 3.5770e-07]
### Epoch 6466 : [3.2484e-05, 9.4591e-05, -6.8792e-07, 3.5683e-07]
### Epoch 6467 : [3.2404e-05, 9.4364e-05, -6.8624e-07, 3.5596e-07]
### Epoch 6468 : [3.2325e-05, 9.4138e-05, -6.8457e-07, 3.5510e-07]
### Epoch 6469 : [3.2245e-05, 9.3912e-05, -6.8290e-07, 3.5424e-07]
### Epoch 6470 : [3.2166e-05, 9.3687e-05, -6.8123e-07, 3.5338e-07]
### Epoch 6471 : [3.2087e-05, 9.3462e-05, -6.7957e-07, 3.5253e-07]
### Epoch 6472 : [3.2008e-05, 9.3238e-05, -6.7792e-07, 3.5167e-07]
### Epoch 6473 : [3.1930e-05, 9.3015e-05, -6.7626e-07, 3.5082e-07]
### Epoch 6474 : [3.1851e-05, 9.2792e-05, -6.7461e-07, 3.4997e

### Epoch 6960 : [9.6388e-06, 2.8896e-05, -2.0584e-07, 1.0761e-07]
### Epoch 6961 : [9.6151e-06, 2.8827e-05, -2.0534e-07, 1.0735e-07]
### Epoch 6962 : [9.5915e-06, 2.8758e-05, -2.0484e-07, 1.0709e-07]
### Epoch 6963 : [9.5679e-06, 2.8689e-05, -2.0434e-07, 1.0683e-07]
### Epoch 6964 : [9.5444e-06, 2.8620e-05, -2.0384e-07, 1.0657e-07]
### Epoch 6965 : [9.5209e-06, 2.8551e-05, -2.0334e-07, 1.0631e-07]
### Epoch 6966 : [9.4975e-06, 2.8483e-05, -2.0285e-07, 1.0605e-07]
### Epoch 6967 : [9.4742e-06, 2.8415e-05, -2.0235e-07, 1.0580e-07]
### Epoch 6968 : [9.4509e-06, 2.8347e-05, -2.0186e-07, 1.0554e-07]
### Epoch 6969 : [9.4277e-06, 2.8279e-05, -2.0136e-07, 1.0528e-07]
### Epoch 6970 : [9.4045e-06, 2.8211e-05, -2.0087e-07, 1.0503e-07]
### Epoch 6971 : [9.3814e-06, 2.8143e-05, -2.0038e-07, 1.0477e-07]
### Epoch 6972 : [9.3584e-06, 2.8076e-05, -1.9989e-07, 1.0452e-07]
### Epoch 6973 : [9.3354e-06, 2.8008e-05, -1.9941e-07, 1.0427e-07]
### Epoch 6974 : [9.3124e-06, 2.7941e-05, -1.9892e-07, 1.0401e

### Epoch 7459 : [2.8224e-06, 8.7229e-06, -6.0817e-08, 3.2055e-08]
### Epoch 7460 : [2.8155e-06, 8.7020e-06, -6.0668e-08, 3.1978e-08]
### Epoch 7461 : [2.8086e-06, 8.6812e-06, -6.0520e-08, 3.1901e-08]
### Epoch 7462 : [2.8017e-06, 8.6603e-06, -6.0372e-08, 3.1823e-08]
### Epoch 7463 : [2.7948e-06, 8.6396e-06, -6.0225e-08, 3.1746e-08]
### Epoch 7464 : [2.7879e-06, 8.6189e-06, -6.0078e-08, 3.1669e-08]
### Epoch 7465 : [2.7810e-06, 8.5982e-06, -5.9932e-08, 3.1592e-08]
### Epoch 7466 : [2.7742e-06, 8.5776e-06, -5.9785e-08, 3.1515e-08]
### Epoch 7467 : [2.7674e-06, 8.5570e-06, -5.9639e-08, 3.1440e-08]
### Epoch 7468 : [2.7606e-06, 8.5365e-06, -5.9494e-08, 3.1363e-08]
### Epoch 7469 : [2.7538e-06, 8.5160e-06, -5.9349e-08, 3.1287e-08]
### Epoch 7470 : [2.7470e-06, 8.4956e-06, -5.9204e-08, 3.1211e-08]
### Epoch 7471 : [2.7402e-06, 8.4753e-06, -5.9059e-08, 3.1135e-08]
### Epoch 7472 : [2.7335e-06, 8.4549e-06, -5.8915e-08, 3.1060e-08]
### Epoch 7473 : [2.7268e-06, 8.4347e-06, -5.8771e-08, 3.0984e

### Epoch 7959 : [8.2358e-07, 2.6272e-06, -1.7916e-08, 9.5227e-09]
### Epoch 7960 : [8.2156e-07, 2.6209e-06, -1.7872e-08, 9.4988e-09]
### Epoch 7961 : [8.1953e-07, 2.6146e-06, -1.7829e-08, 9.4767e-09]
### Epoch 7962 : [8.1752e-07, 2.6083e-06, -1.7785e-08, 9.4544e-09]
### Epoch 7963 : [8.1550e-07, 2.6021e-06, -1.7742e-08, 9.4319e-09]
### Epoch 7964 : [8.1350e-07, 2.5958e-06, -1.7698e-08, 9.4092e-09]
### Epoch 7965 : [8.1149e-07, 2.5896e-06, -1.7655e-08, 9.3863e-09]
### Epoch 7966 : [8.0950e-07, 2.5834e-06, -1.7612e-08, 9.3634e-09]
### Epoch 7967 : [8.0750e-07, 2.5772e-06, -1.7569e-08, 9.3401e-09]
### Epoch 7968 : [8.0552e-07, 2.5710e-06, -1.7526e-08, 9.3167e-09]
### Epoch 7969 : [8.0353e-07, 2.5649e-06, -1.7483e-08, 9.2948e-09]
### Epoch 7970 : [8.0156e-07, 2.5587e-06, -1.7441e-08, 9.2729e-09]
### Epoch 7971 : [7.9958e-07, 2.5526e-06, -1.7398e-08, 9.2508e-09]
### Epoch 7972 : [7.9761e-07, 2.5465e-06, -1.7356e-08, 9.2284e-09]
### Epoch 7973 : [7.9565e-07, 2.5404e-06, -1.7313e-08, 9.2060e

### Epoch 8458 : [2.4065e-07, 7.9324e-07, -5.2888e-09, 2.8390e-09]
### Epoch 8459 : [2.4006e-07, 7.9134e-07, -5.2757e-09, 2.8321e-09]
### Epoch 8460 : [2.3946e-07, 7.8944e-07, -5.2630e-09, 2.8251e-09]
### Epoch 8461 : [2.3888e-07, 7.8755e-07, -5.2503e-09, 2.8181e-09]
### Epoch 8462 : [2.3829e-07, 7.8566e-07, -5.2374e-09, 2.8110e-09]
### Epoch 8463 : [2.3770e-07, 7.8378e-07, -5.2247e-09, 2.8039e-09]
### Epoch 8464 : [2.3711e-07, 7.8190e-07, -5.2118e-09, 2.7967e-09]
### Epoch 8465 : [2.3653e-07, 7.8003e-07, -5.1989e-09, 2.7894e-09]
### Epoch 8466 : [2.3595e-07, 7.7816e-07, -5.1860e-09, 2.7821e-09]
### Epoch 8467 : [2.3537e-07, 7.7629e-07, -5.1735e-09, 2.7747e-09]
### Epoch 8468 : [2.3479e-07, 7.7443e-07, -5.1610e-09, 2.7673e-09]
### Epoch 8469 : [2.3421e-07, 7.7258e-07, -5.1485e-09, 2.7600e-09]
### Epoch 8470 : [2.3363e-07, 7.7072e-07, -5.1359e-09, 2.7524e-09]
### Epoch 8471 : [2.3305e-07, 7.6888e-07, -5.1233e-09, 2.7466e-09]
Done !
[ 0.99382215  2.02722417  4.01749946 10.00850448]


# Sphere plot

In [5]:
# Now that we have the center (x, y, z) and the radius (r) for our sphere,
# we can generated its surface using plotly. 

#Plotting the sphere
Data = []
_,X, Y, Z = mGeneratePointsFromSphere(T, 10*nPoints)
    
trace = go.Surface(
            x=X,
            y=Y,
            z=Z,
            showscale=False,
            opacity = 0.5,
            colorscale=[[0, 'rgb(0,0,100)'], [1, 'rgb(0,0,100)']])

trace2=go.Scatter3d(
           x=sphPoints[:,0].ravel(),
           y=sphPoints[:,1].ravel(),
           z=sphPoints[:,2].ravel(),
           mode='markers',
           name='points',
           marker=go.Marker(symbol='dot',
                            size=5,
                            color='rgb(185,50,50)',
                            opacity=0.9),)

Data.append(trace)
Data.append(trace2)

layout = go.Layout(
            title="Sphere fit",
            scene=go.Scene(
                aspectmode = "data",
                xaxis=go.XAxis(dict(title="x(mm)")),
                yaxis=go.YAxis(dict(title="y(mm)")),
                zaxis=go.ZAxis(dict(title="z(mm)")),              
                camera=dict(
                       up=dict(x=0, y=0, z=0),
                       center=dict(x=0, y=0, z=0),
                       eye=dict(x=0, y=-0.001, z=-2.5)))) 



fig = go.Figure(data=Data, layout=layout)
py.iplot(fig, filename='')